In [53]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-
"""
PROJEKT ZALICZENIOWY: ANALIZA SPEKTRALNA
Dane: Bitcoin BTC/USD (2010-2025)
"""



'\nPROJEKT ZALICZENIOWY: ANALIZA SPEKTRALNA\nDane: Bitcoin BTC/USD (2010-2025)\n'

# PROJEKT ZALICZENIOWY: ANALIZA SPEKTRALNA

**Antoni Kois**

**Dane:** Bitcoin BTC/USD (btcusd_day.csv, 2010-2025)

**Zakres:** 2010-2025, ~5600 obserwacji

In [54]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy import signal, stats
from scipy.fft import fft, fftfreq
from statsmodels.tsa.stattools import adfuller
from statsmodels.tsa.filters.hp_filter import hpfilter
from astropy.timeseries import LombScargle
import warnings

warnings.filterwarnings("ignore")

# PRZYGOTOWANIE DANYCH

In [55]:
# Wczytanie danych
df = pd.read_csv(
    "btcusd_day.csv", usecols=["datetime", "close"], parse_dates=["datetime"]
)
df.set_index("datetime", inplace=True)
df.sort_index(inplace=True)
df = df.dropna()

print(f"Dane: {df.index[0].date()} - {df.index[-1].date()}, N={len(df)}")

Dane: 2010-07-17 - 2025-11-21, N=5607


Mamy dokładnie 5607 dni - obserwacji

In [56]:
# Wizualizacja cen
fig = go.Figure()
fig.add_trace(go.Scatter(x=df.index, y=df["close"], mode="lines", name="Cena BTC/USD"))
fig.update_layout(
    title="Cena zamknięcia Bitcoin",
    xaxis_title="Data",
    yaxis_title="Cena (USD)",
    height=400,
)
fig.show()

Widzimy, iż wzrosty Bitcoina na przestrzeni lat były ogromne. Specialnie nie używam skali logarytmicznej by móc pokazać skalę z jakimi danymi mamy do czynienia.
Teraz przejdziemy do badania stacjonarności naszych danych. Odrazu z góry można przypuszczać, że cena będzie prawdopodobnie niestacjonarna, jednak by się upewnić, przeprowadzimy odpowiednie testy, a dokładniej test ADF, gdzie potem na podsatwie p-value zdecydujemy czy odrzucamy tezę H0 czy nie.

In [57]:
# Test stacjonarności
def test_adf(series, nazwa):
    result = adfuller(series.dropna(), autolag="AIC")
    print(f"\n{nazwa}:")
    print(f"ADF statystyka: {result[0]:.4f}")
    print(f"p-wartość: {result[1]:.4f}")
    print(f"Wniosek: {'STACJONARNY' if result[1] < 0.05 else 'NIESTACJONARNY'}")
    return result[1] < 0.05


# Test dla cen
is_stat_price = test_adf(df["close"], "Ceny oryginalne")

# Test dla logarytmicznych zwrotów
df["log_returns"] = np.log(df["close"]).diff()
is_stat_returns = test_adf(df["log_returns"].dropna(), "Logarytmiczne zwroty")

# Wybór danych stacjonarnych
if is_stat_returns:
    data_stacjonarne = df["log_returns"].dropna()
    metoda = "Logarytmiczne zwroty"
else:
    # Filtr HP jeśli niestacjonarne
    hp_cycle, _ = hpfilter(np.log(df["close"]).dropna(), lamb=6_400_000)
    data_stacjonarne = hp_cycle
    metoda = "Filtr HP"

print(f"Liczba obserwacji po usunięciu `na`: {len(data_stacjonarne)}")


Ceny oryginalne:
ADF statystyka: -0.9434
p-wartość: 0.7733
Wniosek: NIESTACJONARNY

Logarytmiczne zwroty:
ADF statystyka: -12.8864
p-wartość: 0.0000
Wniosek: STACJONARNY
Liczba obserwacji po usunięciu `na`: 5606


Jak też widzimy po wynikach testu na stacjonarności, nie musimy już więcej przygotowyać danych poza tym, że cenę przeliczyliśmy na logarytmiczne zwroty.

Logarytmiczne zwroty już okazały się stacjonarne, dlatego nie zastosuję już więcej transformacji, które miały by za zadanie pomóc w osiągnięciu stacjonarności czy choćby filtry HP/CF.

In [58]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=data_stacjonarne.index,
        y=data_stacjonarne.values,
        mode="lines",
        name=metoda,
        line=dict(width=0.8),
    )
)
fig.add_hline(y=0, line_dash="dash", line_color="red")
fig.update_layout(
    title=metoda,
    xaxis_title="Data",
    yaxis_title="Zwrot",
    height=400,
)
fig.show()

# 1. ANALIZA PODSTAWOWA

## 1.1 DFT i periodogram: oryginalne vs scentrowane

In [59]:
# Funkcje pomocnicze
def compute_dft(x):
    return fft(x)


# Według wzoru z wykładów
def naive_periodogram(x):
    N = len(x)
    X = fft(x)
    power = (1 / N) * np.abs(X) ** 2
    freqs = fftfreq(N, d=1.0)
    idx = freqs > 0
    return freqs[idx], power[idx]

Teraz przechodzimy do fazy scentrowania danych, dla upewnienia wyświetlę też średnią naszych nowych i starych danych

In [60]:
# Dane
x_original = data_stacjonarne.values
x_centered = x_original - np.mean(x_original)

print(f"Średnia danych oryginalnych: {np.mean(x_original):.6f}")
print(f"Średnia danych scentrowanych: {np.mean(x_centered):.6f}")

# DFT
dft_orig = compute_dft(x_original)
dft_cent = compute_dft(x_centered)

# Periodogramy
freqs_orig, power_orig = naive_periodogram(x_original)
freqs_cent, power_cent = naive_periodogram(x_centered)

Średnia danych oryginalnych: 0.002561
Średnia danych scentrowanych: -0.000000


In [61]:
# Wizualizacja DFT
fig = make_subplots(
    rows=1, cols=2, subplot_titles=("DFT - Dane oryginalne", "DFT - Dane scentrowane")
)

fig.add_trace(
    go.Scatter(
        y=np.abs(dft_orig[: len(dft_orig) // 2]), mode="lines", name="Oryginalne"
    ),
    row=1,
    col=1,
)
fig.add_trace(
    go.Scatter(
        y=np.abs(dft_cent[: len(dft_cent) // 2]),
        mode="lines",
        name="Scentrowane",
        line=dict(color="red"),
    ),
    row=1,
    col=2,
)

fig.update_yaxes(type="log", title_text="Amplituda", row=1, col=1)
fig.update_yaxes(type="log", title_text="Amplituda", row=1, col=2)
fig.update_xaxes(title_text="Indeks częstotliwości", row=1, col=1)
fig.update_xaxes(title_text="Indeks częstotliwości", row=1, col=2)
fig.update_layout(height=400, showlegend=False)
fig.show()

Tak jak można było się spodziewać, dane po centrowaniu mają początek w bardzo małej wartości bliskiej zeru, dlatego skala wykresu "DFT - Dane scentrowane" jest tak "rozjechana". Jest to oczekiwane zachowanie, więc nie powinniśmy się temu zjawisku dziwić.

Teraz przechodzimy do zbudowania pierwszych naiwnych periodogramów.

In [62]:
# Wizualizacja periodogramów
fig = make_subplots(
    rows=1,
    cols=2,
    subplot_titles=("Periodogram - Oryginalne", "Periodogram - Scentrowane"),
)

fig.add_trace(
    go.Scatter(x=freqs_orig, y=power_orig, mode="lines", name="Oryginalne"),
    row=1,
    col=1,
)
fig.add_trace(
    go.Scatter(
        x=freqs_cent,
        y=power_cent,
        mode="lines",
        name="Scentrowane",
        line=dict(color="red"),
    ),
    row=1,
    col=2,
)

fig.update_yaxes(type="log", title_text="Moc", row=1, col=1)
fig.update_yaxes(type="log", title_text="Moc", row=1, col=2)
fig.update_xaxes(title_text="Częstotliwość", row=1, col=1)
fig.update_xaxes(title_text="Częstotliwość", row=1, col=2)
fig.update_layout(height=400, showlegend=False)
fig.show()

Centrowanie usuwa składową DC (f=0), ale nie wpływa na widmo dla f>0, dlatego oba periodogramy są można rzec, że identyczne.

## 1.2 Eksperyment z długością N



Do eksperymentu z liczbą obserwacji, ustawimy tą liczbę na 7, gdyż jest to naturalna liczba dni w tygodniu, dlatego ją wybrałem.

In [63]:
natural_period = 7  # tydzień
N_full = len(x_centered)
N_div = (N_full // natural_period) * natural_period
N_nondiv = N_div + 1

x_div = x_centered[:N_div]
x_nondiv = x_centered[:N_nondiv]

freqs_div, power_div = naive_periodogram(x_div)
freqs_nondiv, power_nondiv = naive_periodogram(x_nondiv)

print(f"N podzielne przez {natural_period}: {N_div}")
print(f"N niepodzielne: {N_nondiv}")

N podzielne przez 7: 5600
N niepodzielne: 5601


Liczbę obserwacji zaokrąglamy dla podzielnego przypadku do 5600, natomiast dla niepodzielnego przez N do 5601.

In [64]:
fig = make_subplots(
    rows=2,
    cols=1,
    subplot_titles=(f"N={N_div} (podzielne)", f"N={N_nondiv} (niepodzielne)"),
)

fig.add_trace(
    go.Scatter(x=freqs_div, y=power_div, mode="lines", name="Podzielne"), row=1, col=1
)
fig.add_trace(
    go.Scatter(
        x=freqs_nondiv,
        y=power_nondiv,
        mode="lines",
        name="Niepodzielne",
        line=dict(color="orange"),
    ),
    row=2,
    col=1,
)

freq_nat = 1 / natural_period
fig.add_vline(x=freq_nat, line_dash="dash", line_color="red", row=1, col=1)
fig.add_vline(x=freq_nat, line_dash="dash", line_color="red", row=2, col=1)

fig.update_yaxes(type="log", title_text="Moc", row=1, col=1)
fig.update_yaxes(type="log", title_text="Moc", row=2, col=1)
fig.update_xaxes(title_text="Częstotliwość", range=[0, 0.5], row=2, col=1)
fig.update_layout(height=600, showlegend=False)
fig.show()

print(
    f"\nKOMENTARZ: N podzielne minimalizuje przeciek spektralny dla okresu {natural_period} dni"
)




KOMENTARZ: N podzielne minimalizuje przeciek spektralny dla okresu 7 dni


Przeprowadzony eksperyment miał pokazać działanie tz. "Przecieku Spektralnego".

W praktyce, ze względu na stochastyczny charakter stóp zwrotu Bitcoina (brak dominującej składowej okresowej), różnice wizualne są niewielkie. Nie udało się tego zjawiska zaobserwować.

Idealnie jak wiemy, powinno to wyglądać w ten sposób, że "piki" np okresu 7 dniowego, na periodogramie drugim powinny być bardziej wypłaszczone.
Po zbliżeniu wykresów na zazanczoną przerywaną linię (okres 7 dni), nieststy nie udaje się zaobserwować tego zjawiska.

# 2. PORÓWNANIE METOD

## 2.1 Periodogram z 95% przedziałem ufności

In [65]:
# Metoda pomocnicza do obliczenia periodogramu z przedziałami ufności

def periodogram_with_ci(x, alpha=0.05):
    freqs, power = naive_periodogram(x)
    chi2_lower = stats.chi2.ppf(alpha / 2, 2)
    chi2_upper = stats.chi2.ppf(1 - alpha / 2, 2)
    ci_lower = power * (2 / chi2_upper)
    ci_upper = power * (2 / chi2_lower)
    return freqs, power, ci_lower, ci_upper


freqs_ci, power_ci, ci_lower, ci_upper = periodogram_with_ci(x_centered)

In [66]:
fig = go.Figure()

fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=ci_upper,
        mode="lines",
        line=dict(width=0),
        showlegend=False,
        hoverinfo="skip",
    )
)
fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=ci_lower,
        mode="lines",
        fill="tonexty",
        fillcolor="rgba(173, 216, 230, 1.0)",
        line=dict(width=0),
        showlegend=False,
        hoverinfo="skip",
    )
)

fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_ci,
        mode="lines",
        name="Periodogram",
        line=dict(color="blue", width=1.5),
    )
)
fig.update_layout(
    title="Periodogram naiwny z 95% przedziałem ufności",
    xaxis_title="Częstotliwość",
    yaxis_title="Moc",
    yaxis_type="log",
    height=400,
)
fig.show()

## 2.2 Periodogram Welcha

Teraz zastosujemy metodę Welcha w celu zmniejszenia wariancji (zredukowania "szumu") na wykresie widma mocy.
Zwykły periodogram ("naiwny") jest estymatorem nieobciążonym, ale niestabilnym. Oznacza to, że ma ogromną wariancję. W praktyce, wykres "skakcze" góra-dół co też możemy zaobserwować w naszym przykładzie.
Metoda Welcha dzieli szereg czasowy na krótsze, nakładające się na siebie segmenty (np. po 256 lub 512 próbek).
Dla każdego segmentu liczy osobny periodogram, a na końcu uśrednia te wyniki i wynikowo otrzymujemy bardziej stabilny wykres widma mocy.
Dzięki uśrednianiu, przypadkowe fluktuacje (szum) się znoszą, a prawdziwy kształt widma zostaje wygładzony.
Wykres staje się czytelniejszy i bardziej wiarygodny statystycznie.

W celu zobrazowania wpływu wiekości próbki na widmo mocy, zastosujemy metodę Welcha z różną wielkością próbki.
- wariant 1: 1024 próbek
- wariant 2: 512 próbek
- wariant 3: 256 próbek
- wariant 4: 124 próbek

Dlsz wszytskich próbek zastosujemy nachodzenie ustawione na 50%

In [67]:
nperseg1 = min(1024, len(x_centered) // 2)
freqs_welch1024, power_welch1024 = signal.welch(
    x_centered, fs=1.0, nperseg=nperseg1, noverlap=nperseg1 // 2
)

nperseg2 = min(512, len(x_centered) // 4)
freqs_welch512, power_welch512 = signal.welch(
    x_centered, fs=1.0, nperseg=nperseg2, noverlap=nperseg2 // 2
)

nperseg3 = min(256, len(x_centered) // 8)
freqs_welch256, power_welch256 = signal.welch(
    x_centered, fs=1.0, nperseg=nperseg3, noverlap=int(nperseg4 * 0.50)
)

nperseg4 = 124
freqs_welch124, power_welch124 = signal.welch(
    x_centered, fs=1.0, nperseg=nperseg4, noverlap=int(nperseg4 * 0.50)
)

freqs_welch = freqs_welch512
power_welch = power_welch512


In [85]:
fig = make_subplots(
    rows=2,
    cols=2,
    subplot_titles=(
        f"Welch: seg={nperseg1}, 50%",
        f"Welch: seg={nperseg2}, 50%",
        f"Welch: seg={nperseg3}, 50%",
        f"Welch: seg={nperseg4}, 50%",
    ),
)

fig.add_trace(
    go.Scatter(
        x=freqs_welch1024,
        y=power_welch1024,
        mode="lines",
        name="W1 (1024)",
        line=dict(color="#1f77b4"),
    ),
    row=1,
    col=1,
)
fig.add_trace(
    go.Scatter(
        x=freqs_welch512,
        y=power_welch512,
        mode="lines",
        name="W2 (512)",
        line=dict(color="#d62728"),
    ),
    row=1,
    col=2,
)
fig.add_trace(
    go.Scatter(
        x=freqs_welch256,
        y=power_welch256,
        mode="lines",
        name="W3 (256)",
        line=dict(color="#2ca02c"),
    ),
    row=2,
    col=1,
)
fig.add_trace(
    go.Scatter(
        x=freqs_welch124,
        y=power_welch124,
        mode="lines",
        name="W4 (124)",
        line=dict(color="#ff7f0e"),
    ),
    row=2,
    col=2,
)

fig.update_yaxes(type="log", title_text="Moc", row=1, col=1)
fig.update_yaxes(type="log", title_text="Moc", row=1, col=2)
fig.update_yaxes(type="log", title_text="Moc", row=2, col=1)
fig.update_yaxes(type="log", title_text="Moc", row=2, col=2)
fig.update_xaxes(title_text="Częstotliwość", row=2, col=1)
fig.update_xaxes(title_text="Częstotliwość", row=2, col=2)
fig.update_layout(height=600, showlegend=False)
fig.show()


Możemy zaobserwować, że wy mniejsze próbkowanie powoduje wygładzanie się periodogramu, co też było spodziewane.
Jest to logiczne, że im więcej próbek nałożymy na siebie, to tym bardziej pojedynczy outliner będzie miał mniejszy wpływ na wygląd periodogramu.
Zyskujemy dzięki temu większą przejrzystość i łatwiej jest analizowac wykres, jednak tracimy pewną część informacji.

In [ ]:
# Porównanie wszystkich wariantów Welcha
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=freqs_welch1024,
        y=power_welch1024,
        mode="lines",
        name="Welch 1024, 25%",
        line=dict(color="#1f77b4", width=0.7),
    )
)
fig.add_trace(
    go.Scatter(
        x=freqs_welch512,
        y=power_welch512,
        mode="lines",
        name="Welch 512, 50%",
        line=dict(color="#d62728", width=0.7),
    )
)
fig.add_trace(
    go.Scatter(
        x=freqs_welch256,
        y=power_welch256,
        mode="lines",
        name="Welch 256, 75%",
        line=dict(color="#2ca02c", width=0.7),
    )
)
fig.add_trace(
    go.Scatter(
        x=freqs_welch124,
        y=power_welch124,
        mode="lines",
        name="Welch 124, 50%",
        line=dict(color="#ff7f0e", width=0.7),
    )
)

fig.update_layout(
    title="Porównanie wariantów Welcha (wysoki kontrast)",
    xaxis_title="Częstotliwość",
    yaxis_title="Moc",
    yaxis_type="log",
    height=400,
)
fig.show()

Do dalszej analizy wykorzystamy periodogramy powstałe z próbkowania:

- 256
- 512

Wybrałem je, gdyż moim zdaniem zachowują najlepiej balans między "szumem", a zbyt dużym wygładzeniem danych, co pozwala w lepszy sposób analizować wykresy.
By móc widzieć faktyczną różnicę, teraz przedstawię wszytskie warianty próbek na jednym wykresie.
Przypomnę także, że wykresy są interaktywne, tak więc można "wyklikać" poprzez legędę np. tylko dwie serie widoczne.

## 2.3 Wygładzanie oknem Daniella


Okno Daniella to w najprostszym ujęciu średnia ruchoma zastosowana na wykresie periodogramu (na widmie częstotliwości).

Parametr `m` określa, ile sąsiednich częstotliwości bierzemy do średniej.
Np. dla `m=5` bierzemy punkt środkowy + 5 z lewej + 5 z prawej. Razem uśredniamy 11 słupków.
Dzięki temu, ta metoda daje delikatne wygładzenie (zachowuje ostre piki).

Parametr "poziomy" (1-poz vs 3-poz) to po prostu krotność zastosowania tego samego filtra.

1-poziomowe: Zwykła średnia arytmetyczna z okna. Wszystkie punkty w oknie są tak samo ważne.

3-poziomowe (Ważone): To jakby w przybliżeniu zastosowanie filtra Daniella trzy razy pod rząd.
Dzięki temu unkty blisko środka okna stają się ważniejsze, a te na brzegach mniej ważne (wagi układają się w kształt dzwonu Gaussa). Daje to bardziej naturalny, gładszy wykres niż wersja 1-poziomowa, która czasem wygląda "schodkowo".

Dla naszego projektu zastosujemy takie kombinację:

- m=5 1-poziomowe
- m=5 3-poziomowe
- m=10 1-poziomowe
- m=10 3-poziomowe

In [ ]:
def daniell_smooth(periodogram, m, levels=1):
    smoothed = periodogram.copy()
    for _ in range(levels):
        window = np.ones(2 * m + 1) / (2 * m + 1)
        smoothed = np.convolve(smoothed, window, mode="same")
    return smoothed

# m=5
m1 = 5
power_daniell_5_1 = daniell_smooth(power_ci, m=m1, levels=1)
power_daniell_5_3 = daniell_smooth(power_ci, m=m1, levels=3)

# m=10
m2 = 10
power_daniell_10_1 = daniell_smooth(power_ci, m=m2, levels=1)
power_daniell_10_3 = daniell_smooth(power_ci, m=m2, levels=3)

# Dla kompatybilności z resztą kodu
power_daniell_1 = power_daniell_5_1
power_daniell_3 = power_daniell_5_3

Okno Daniella: m=5, szerokość=11
Okno Daniella: m=10, szerokość=21


In [ ]:
fig = make_subplots(
    rows=2,
    cols=2,
    subplot_titles=(
        f"Daniell m={m1}, 1-poz",
        f"Daniell m={m1}, 3-poz",
        f"Daniell m={m2}, 1-poz",
        f"Daniell m={m2}, 3-poz",
    ),
)

fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_daniell_5_1,
        mode="lines",
        name="D5-1",
        line=dict(color="#1f77b4"),
    ),
    row=1,
    col=1,
)
fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_daniell_5_3,
        mode="lines",
        name="D5-3",
        line=dict(color="#d62728"),
    ),
    row=1,
    col=2,
)
fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_daniell_10_1,
        mode="lines",
        name="D10-1",
        line=dict(color="#2ca02c"),
    ),
    row=2,
    col=1,
)
fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_daniell_10_3,
        mode="lines",
        name="D10-3",
        line=dict(color="#ff7f0e"),
    ),
    row=2,
    col=2,
)

fig.update_yaxes(type="log", title_text="Moc", row=1, col=1)
fig.update_yaxes(type="log", title_text="Moc", row=1, col=2)
fig.update_yaxes(type="log", title_text="Moc", row=2, col=1)
fig.update_yaxes(type="log", title_text="Moc", row=2, col=2)
fig.update_xaxes(title_text="Częstotliwość", row=2, col=1)
fig.update_xaxes(title_text="Częstotliwość", row=2, col=2)
fig.update_layout(height=600, showlegend=False)
fig.show()

Odrazu na pierwszy rzut oka, wykresy te wyglądają bardziej czytelnie niż wykresy stworzone z użyciem metody Welcha.
Możemy w łatwy sposób wizualnie oddzielić trendy spadkowy/wzrostowy oraz szczyty i dołki.

Widzimy iż:
- zwiększanie parametru `m`, czyli można rzec ilości branych obserwacji, zachowuje się podobnie jak w przypadku Welcha, czyli zwiększa wygłądzenie wykresu
- podobne oddziaływnaie widimy w zastosowaniu `poziomów`, wraz ze wzrostem, wykres pozbywa się charakteru szumu, a bardziej zaczya przypominać wykres z sezonowością (wspomiane pokazanie się trendu, szczytów i dołków)

In [ ]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_daniell_5_1,
        mode="lines",
        name=f"Daniell m={m1}, 1-poz",
        line=dict(color="#1f77b4", width=0.7),
    )
)
fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_daniell_5_3,
        mode="lines",
        name=f"Daniell m={m1}, 3-poz",
        line=dict(color="#d62728", width=0.7),
    )
)
fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_daniell_10_1,
        mode="lines",
        name=f"Daniell m={m2}, 1-poz",
        line=dict(color="#2ca02c", width=0.7),
    )
)
fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_daniell_10_3,
        mode="lines",
        name=f"Daniell m={m2}, 3-poz",
        line=dict(color="#ff7f0e", width=0.7),
    )
)

fig.update_layout(
    title="Porównanie wariantów Daniella (wysoki kontrast)",
    xaxis_title="Częstotliwość",
    yaxis_title="Moc",
    yaxis_type="log",
    height=400,
)
fig.show()



Po porównaniu 4 konfiguracji metody okna Daniela, zdecydowałem, że w dalszej analizię będziemy korzystać z konfiguracji:

- m=5 3-poziomowe
- m=10 1-poziomowe

Skupimy się na nich z tego samego powodu jak w przypadku meotdy Welcha, gdyż są one odpowiednim balansem między zbut dużą utratą poierwotnego kształtu, a zbyt małym wpływem.

## 2.4 Wygładzanie manualne (uśrednianie podokresów)




In [92]:
def manual_average(x, n_seg=10):
    N = len(x)
    seg_len = N // n_seg
    x_trim = x[: seg_len * n_seg]
    segments = np.array_split(x_trim, n_seg)
    periodograms = [naive_periodogram(seg)[1] for seg in segments]
    freqs_avg, _ = naive_periodogram(segments[0])
    return freqs_avg, np.mean(periodograms, axis=0)


freqs_manual, power_manual = manual_average(x_centered, n_seg=10)

In [94]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=freqs_manual,
        y=power_manual,
        mode="lines",
        name="Manualny",
        line=dict(color="purple"),
    )
)
fig.update_layout(
    title="Periodogram - wygładzanie manualne (10 podokresów)",
    xaxis_title="Częstotliwość",
    yaxis_title="Moc",
    yaxis_type="log",
    height=400,
)
fig.show()

## 2.5 Porównanie wszystkich metod



In [95]:
fig = go.Figure()
# 1. Naiwny
fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_ci,
        mode="lines",
        name="Naiwny",
        line=dict(color="gray", width=0.7),
        opacity=0.4,
    )
)
# 2. Welch 512
fig.add_trace(
    go.Scatter(
        x=freqs_welch512,
        y=power_welch512,
        mode="lines",
        name="Welch 512",
        line=dict(color="#d62728", width=0.8),
    )
)
# 3. Welch 256
fig.add_trace(
    go.Scatter(
        x=freqs_welch256,
        y=power_welch256,
        mode="lines",
        name="Welch 256",
        line=dict(color="#2ca02c", width=0.8),
    )
)
# 4. Daniell 10 1-poz
fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_daniell_10_1,
        mode="lines",
        name="Daniell 10 (1-poz)",
        line=dict(color="#1f77b4", width=0.8),
    )
)
# # 5. Daniell 10 3-poz
# fig.add_trace(
#     go.Scatter(
#         x=freqs_ci,
#         y=power_daniell_10_3,
#         mode="lines",
#         name="Daniell 10 (3-poz)",
#         line=dict(color="maroon", width=0.8),
#     )
# )
# 6. Daniell 5 3-poz
fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_daniell_5_3,
        mode="lines",
        name="Daniell 5 (3-poz)",
        line=dict(color="red", width=0.8),
    )
)
# 7. Manualny
fig.add_trace(
    go.Scatter(
        x=freqs_manual,
        y=power_manual,
        mode="lines",
        name="Manualny",
        line=dict(color="purple", width=0.8),
    )
)

fig.update_layout(
    title="Porównanie wybranych metod estymacji (Final)",
    xaxis_title="Częstotliwość",
    yaxis_title="Moc",
    yaxis_type="log",
    height=600,
)
fig.show()

Wszystkie metody, mimo różnic w gładkości, pokazują ten sam ogólny trend. Brak dominującego szczytu. Widmo jest w miarę płaskie z lekkimi szczytami, co potwierdza hipotezę, że log-zwroty Bitcoina przypominają bardziej szum (bliski białego) niż jakąś sztywną cykliczność. Nie ozancza to jednak iż nie możemy zauważyć lokalnych szczytów jak np. ten w okolicach ~0.19, czy ~0.35, oraz dołków w okolicach ~0.14, czy ~0.25.

Metoda Welcha (Linie: Zielona i Czerwona):
Wykazuje tędęcje do większego wygładzenia (najmniejszej wariancji), w szczególności konfiguracja Welcha dla 256 próbek. Linia jest stabilna i nie "skacze" tak gwałtownie jak inne. Jednakże, ma ona też tendencję do przeszacowywania mocy (leży wyraźnie wyżej niż pozostałe metody na wykresie). Wynika to z faktu, że Welch uśrednia energię z wielu nakładających się okien, co przy krótkich segmentach (256/512) i silnym wygładzaniu może podbijać poziom tła.

Okno Daniella (Linie: Niebieska i Pomarańczowa)
Daje najlepszy kompromis.
Daniell 5 (3-poz, Pomarańczowa): Bardzo dobrze podąża za lokalnymi trendami, wygładzając szum, ale nie tracąc informacji o strukturze widma. Nie jest tak "płaski" jak Welch, ale znacznie czytelniejszy niż periodogram surowy (Manualny).
Daniell 10 (1-poz, Niebieska): Jest nieco bardziej "poszarpany", jednakże kroczy wręcz idealną tę samą ścieżką co Daniell 5 z poziomem 3.

Wygładzanie Manualne (Linia: Fioletowa)
Jest najbardziej "poszarpana" i zmienna.
Stanowi dobrą linię bazową (referencję), pokazując, gdzie realnie oscyluje energia sygnału bez agresywnego filtrowania.
Widać, że metody Daniella oscylują wokół linii manualnej, podczas gdy Welch leży zauważalnie wyżej.

# 3. DANE NIEKOMPLETNE

## 3.1 Symulacja braków (30%)



In [76]:
np.random.seed(42)
df_complete = pd.DataFrame(
    {"value": x_centered}, index=data_stacjonarne.index[: len(x_centered)]
)
n_remove = int(0.3 * len(df_complete))
indices_remove = np.random.choice(df_complete.index, size=n_remove, replace=False)
df_incomplete = df_complete.drop(indices_remove)

print(f"Usunięto {n_remove} obs. ({100*n_remove/len(df_complete):.1f}%)")
print(f"Pozostało: {len(df_incomplete)} obs.")



Usunięto 1681 obs. (30.0%)
Pozostało: 3925 obs.


In [77]:
fig = make_subplots(
    rows=2,
    cols=1,
    subplot_titles=(
        "Dane kompletne",
        "Dane: pozostałe (niebieskie) i usunięte (czerwone)",
    ),
)

fig.add_trace(
    go.Scatter(
        x=df_complete.index,
        y=df_complete["value"],
        mode="lines",
        name="Kompletne",
        line=dict(color="blue", width=0.8),
    ),
    row=1,
    col=1,
)

# Dane pozostałe (70%)
fig.add_trace(
    go.Scatter(
        x=df_incomplete.index,
        y=df_incomplete["value"],
        mode="markers",
        name="Pozostałe (70%)",
        marker=dict(size=3, color="blue"),
    ),
    row=2,
    col=1,
)

# Dane usunięte (30%)
df_removed = df_complete.loc[indices_remove]
fig.add_trace(
    go.Scatter(
        x=df_removed.index,
        y=df_removed["value"],
        mode="markers",
        name="Usunięte (30%)",
        marker=dict(size=3, color="red", symbol="x"),
    ),
    row=2,
    col=1,
)

fig.update_yaxes(title_text="Wartość", row=1, col=1)
fig.update_yaxes(title_text="Wartość", row=2, col=1)
fig.update_xaxes(title_text="Czas", row=2, col=1)
fig.update_layout(height=600, showlegend=True)
fig.show()



## 3.2 Periodogram naiwny (z interpolacją)



In [78]:
df_interp = df_complete.copy()
df_interp.loc[indices_remove, "value"] = np.nan
df_interp["value"] = df_interp["value"].interpolate(method="linear")

freqs_interp, power_interp = naive_periodogram(df_interp["value"].values)

print("Periodogram naiwny (interpolacja liniowa)")



Periodogram naiwny (interpolacja liniowa)


In [79]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=freqs_interp,
        y=power_interp,
        mode="lines",
        name="Naiwny (interpolowany)",
        line=dict(color="orange"),
    )
)
fig.update_layout(
    title="Periodogram naiwny - dane interpolowane",
    xaxis_title="Częstotliwość",
    yaxis_title="Moc",
    yaxis_type="log",
    height=400,
)
fig.show()



## 3.3 Periodogram Lomba-Scargle'a



In [80]:
t_incomplete = (df_incomplete.index - df_incomplete.index[0]).total_seconds() / 86400
y_incomplete = df_incomplete["value"].values

ls = LombScargle(t_incomplete, y_incomplete)
freqs_ls = np.linspace(0.001, 0.5, 5000)
power_ls = ls.power(freqs_ls)

fap_level = 0.05
power_threshold = ls.false_alarm_level(fap_level)

print(f"Lomb-Scargle: próg istotności (FAP=5%) = {power_threshold:.6f}")



Lomb-Scargle: próg istotności (FAP=5%) = 0.006851


In [81]:
fig = go.Figure()
fig.add_trace(
    go.Scatter(
        x=freqs_ls,
        y=power_ls,
        mode="lines",
        name="Lomb-Scargle",
        line=dict(color="green"),
    )
)
fig.add_hline(
    y=power_threshold, line_dash="dash", line_color="red", annotation_text=f"Próg 5%"
)

fig.update_layout(
    title="Periodogram Lomba-Scargle'a - dane niekompletne",
    xaxis_title="Częstotliwość",
    yaxis_title="Moc znormalizowana",
    height=400,
)
fig.show()



## 3.4 Porównanie



In [82]:
fig = go.Figure()

# Normalizacja
power_ci_norm = power_ci / power_ci.max()
power_interp_norm = power_interp / power_interp.max()
power_ls_norm = power_ls / power_ls.max()

fig.add_trace(
    go.Scatter(
        x=freqs_ci,
        y=power_ci_norm,
        mode="lines",
        name="Naiwny (kompletne)",
        line=dict(color="blue", width=0.7),
        opacity=0.7,
    )
)
fig.add_trace(
    go.Scatter(
        x=freqs_interp,
        y=power_interp_norm,
        mode="lines",
        name="Naiwny (interpolowane)",
        line=dict(color="orange", width=0.7),
        opacity=0.7,
    )
)
fig.add_trace(
    go.Scatter(
        x=freqs_ls,
        y=power_ls_norm,
        mode="lines",
        name="Lomb-Scargle",
        line=dict(color="green", width=0.7),
        opacity=0.9,
    )
)
fig.add_hline(
    y=power_threshold / power_ls.max(),
    line_dash="dash",
    line_color="red",
    annotation_text="Próg 5%",
)

fig.update_layout(
    title="Porównanie metod dla danych niekompletnych",
    xaxis_title="Częstotliwość",
    yaxis_title="Moc znormalizowana",
    xaxis_range=[0, 0.5],
    height=500,
)
fig.show()

print("\nKOMENTARZ: Lomb-Scargle >> Naiwny dla danych z brakami")
print("Interpolacja tworzy artefakty - nie zalecana!")




KOMENTARZ: Lomb-Scargle >> Naiwny dla danych z brakami
Interpolacja tworzy artefakty - nie zalecana!


---
# PODSUMOWANIE
---



In [83]:
print("\n" + "=" * 70)
print("PODSUMOWANIE PROJEKTU")
print("=" * 70)
print(
    f"""
ZADANIE 1:
✓ DFT/periodogram: centrowanie usuwa DC, nie wpływa na f>0
✓ Eksperyment N: podzielne minimalizuje przeciek spektralny

ZADANIE 2:
✓ Periodogram + 95% CI (rozkład χ²)
✓ Metoda Welcha - NAJLEPSZA (kompromis wariancja/rozdzielczość)
✓ Daniell (1 i 3 poziomy) - wygładzanie
✓ Manualny (5 podokresów) - uśrednianie

ZADANIE 3:
✓ Braki 30% - symulacja
✓ Naiwny (interpolacja) - problematyczny
✓ Lomb-Scargle - REKOMENDOWANY dla braków
✓ Test istotności 5% (FAP)

WNIOSKI:
- Stacjonarność kluczowa
- Welch dla danych regularnych
- Lomb-Scargle dla braków
- Trade-off: wariancja ↓ ⟺ rozdzielczość ↓
"""
)
print("=" * 70)
print("\n✓ PROJEKT ZAKOŃCZONY")




PODSUMOWANIE PROJEKTU

ZADANIE 1:
✓ DFT/periodogram: centrowanie usuwa DC, nie wpływa na f>0
✓ Eksperyment N: podzielne minimalizuje przeciek spektralny

ZADANIE 2:
✓ Periodogram + 95% CI (rozkład χ²)
✓ Metoda Welcha - NAJLEPSZA (kompromis wariancja/rozdzielczość)
✓ Daniell (1 i 3 poziomy) - wygładzanie
✓ Manualny (5 podokresów) - uśrednianie

ZADANIE 3:
✓ Braki 30% - symulacja
✓ Naiwny (interpolacja) - problematyczny
✓ Lomb-Scargle - REKOMENDOWANY dla braków
✓ Test istotności 5% (FAP)

WNIOSKI:
- Stacjonarność kluczowa
- Welch dla danych regularnych
- Lomb-Scargle dla braków
- Trade-off: wariancja ↓ ⟺ rozdzielczość ↓


✓ PROJEKT ZAKOŃCZONY
